In [1]:
import pandas as pd
import numpy as np
import time
from datetime import timedelta
from decouple import config
import os
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns

In [84]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows',1000)
pd.set_option('display.float_format', lambda x: '%.f' % x)

# Загружаем данные

In [3]:
df_lic_master = pd.read_csv('data/License_Master.csv')
df_lic_activities = pd.read_csv('data/License_Activities.csv')

In [4]:
df_crds = pd.read_excel('data/UAE_all_cards.xlsx')
df_crds

Id карточки  Открыть           Id фирмы  \
0       70000001026874071      NaN  70000001026874070   
1       70000001030694302      NaN  70000001030694301   
2       70000001007241428      NaN  70000001007241429   
3       70000001034833436      NaN  70000001034833435   
4       70000001019449683      NaN  70000001019449682   
...                   ...      ...                ...   
298901  70000001046981925      NaN  70000001019395550   
298902  70000001046133275      NaN  70000001019395550   
298903  70000001047602023      NaN  70000001019395550   
298904  70000001047629158      NaN  70000001019395550   
298905  70000001048026889      NaN  70000001019395550   

                                 Наименование организации  \
0                    Al Bustan Building Cleaning, company   
1       Bawabat Al Najah Documents Typing & Copying, c...   
2               Istorat Al Faan Repairing Jewellery, shop   
3                     Al Zahra Metal & Aluminum, workshop   
4                                  Bombay Gate, cafeteria   
...                                                   ...   
298901                                    Etisalat, store   
298902                                    Etisalat, store   
298903                                    Etisalat, store   
298904                                    Etisalat, store   
298905                                    Etisalat, store   

                                              Бренд Короткое название  \
0                       Al Bustan Building Cleaning               NaN   
1       Bawabat Al Najah Documents Typing & Copying               NaN   
2               Istorat Al Faan Repairing Jewellery               NaN   
3                         Al Zahra Metal & Aluminum               NaN   
4                                       Bombay Gate               NaN   
...                                             ...               ...   
298901                                     Etisalat               NaN   
298902                                     Etisalat               NaN   
298903                                     Etisalat               NaN   
298904                                     Etisalat               NaN   
298905                                     Etisalat               NaN   

       Юридическое название Организационно-правовая форма Не публиковать  \
0                       NaN                           NaN            Нет   
1                       NaN                           NaN            Нет   
2                       NaN                           NaN            Нет   
3                       NaN                           NaN            Нет   
4                       NaN                           NaN            Нет   
...                     ...                           ...            ...   
298901                  NaN                           NaN            Нет   
298902                  NaN                           NaN            Нет   
298903                  NaN                           NaN            Нет   
298904                  NaN                           NaN            Нет   
298905                  NaN                           NaN            Нет   

       Юридическое название филиала Организационно-правовая форма филиала  \
0                               NaN                                   NaN   
1                               NaN                                   NaN   
2                               NaN                                   NaN   
3                               NaN                                   NaN   
4                               NaN                                   NaN   
...                             ...                                   ...   
298901                          NaN                                   NaN   
298902                          NaN                                   NaN   
298903                          NaN                                   NaN   
298904                          NaN 

In [5]:
df_trade_lic = pd.read_csv('data/uae_trade_license.csv')
df_trade_lic

id  source_id     stable_id  \
0      7.000000e+16          1  7.000000e+16   
1      7.000000e+16          1  7.000000e+16   
2      7.000000e+16          1  7.000000e+16   
3      7.000000e+16          1  7.000000e+16   
4      7.000000e+16          1  7.000000e+16   
...             ...        ...           ...   
69810  7.000000e+16          1  7.000000e+16   
69811  7.000000e+16          1  7.000000e+16   
69812  7.000000e+16          1  7.000000e+16   
69813  7.000000e+16          1  7.000000e+16   
69814  7.000000e+16          1  7.000000e+16   

                                                 name       firm_id  \
0                        Total Care Mobile Phones LLC  7.000000e+16   
1                           Smart Tax Consultancy LLC  7.000000e+16   
2                                      Vital Sign LLC  7.000000e+16   
3      Al Shams Al Tahabiah Garments Ironing, laundry  7.000000e+16   
4        Mohammed Kahteeri Gas District Establishment  7.000000e+16   
...                                               ...           ...   
69810                         JF, restaurant and cafe  7.000000e+16   
69811                         Layaly Adan, restaurant  7.000000e+16   
69812        Gulfscape Technical Services Company LLC  7.000000e+16   
69813                           Kanaan Decor, company  7.000000e+16   
69814                           Selex Electricals LLC  7.000000e+16   

                                            firm_name  branch_id tradelicense  \
0                        Total Care Mobile Phones LLC         99   CN-1795648   
1                           Smart Tax Consultancy LLC         99   CN-2433306   
2                                      Vital Sign LLC         99     650350.0   
3      Al Shams Al Tahabiah Garments Ironing, laundry         99     749204.0   
4        Mohammed Kahteeri Gas District Establishment         99   CN-1049336   
...                                               ...        ...          ...   
69810                         JF, restaurant and cafe         99   CN-2289775   
69811                         Layaly Adan, restaurant         99        93749   
69812        Gulfscape Technical Services Company LLC         99       746018   
69813                           Kanaan Decor, company         99   CN-1033065   
69814                           Selex Electricals LLC         99       554414   

             phone  
0      557130040.0  
1      507339118.0  
2        2383278.0  
3      502039685.0  
4              NaN  
...            ...  
69810  523005997.0  
69811    2221227.0  
69812    2659835.0  
69813    5542867.0  
69814    2678714.0  

[69815 rows x 9 columns]

# Анализ связи License Activities and License Master

In [6]:
len(df_lic_activities['license_number'].unique())

529591

In [7]:
df_activities_master = df_lic_master.merge(df_lic_activities.drop_duplicates(), on=['license_number'], how='left', indicator=True)

In [8]:
len(df_activities_master['license_number'].unique())

538471

In [9]:
df_master_notin_activities = df_activities_master[df_activities_master['_merge'] != 'both']

In [10]:
df_master_notin_activities.groupby('license_number').size().sort_values(ascending=False).reset_index(name='count')

license_number  count
0                  0      1
1             209555      1
2             209509      1
3             209516      1
4             209519      1
...              ...    ...
8875          113088      1
8876          113087      1
8877          113086      1
8878          113082      1
8879          825230      1

[8880 rows x 2 columns]

In [11]:
df_lic_activities_gb = pd.DataFrame(df_lic_activities.groupby('license_number').size().sort_values(ascending=False).reset_index(name='count'))

In [13]:
df_lic_activities_gb['count'].sum()

2003918

In [15]:
df_lic_activities_gb['count'].mean()

3.783897384963113

In [12]:
# chart
# sns.load_dataset(df_lic_activities_gb)
ax = sns.barplot(x=df_lic_activities_gb.index, y=df_lic_activities_gb.counts)

NameError: name 'df_lic_activities_gb' is not defined

# Сматчить данные с Trade License с ИР

# Матчинг с лицензиями ИР

In [16]:
df_trade_lic['tradelicense_pure'] = df_trade_lic['tradelicense']

In [34]:
df_trade_lic['tradelicense_pure'] = df_trade_lic['tradelicense_pure'].astype(str)
df_lic_master['trade_name_serial_number'] = df_lic_master['trade_name_serial_number'].astype(str)
df_lic_master['license_number'] = df_lic_master['license_number'].astype(str)

In [35]:
df_trade_lic['tradelicense_pure_w0'] = df_trade_lic['tradelicense_pure'].str.replace("\.0", "")
df_trade_lic['tradelicense_pure_w0andCN']  = df_trade_lic['tradelicense_pure_w0'].str.replace("CN-", "")
df_trade_lic['tradelicense_pure_w0andCN'] = df_trade_lic['tradelicense_pure_w0andCN'].astype(str)

/var/folders/5b/cfgbcxjj0n30b2ljslhwkz9mndjsxd/T/ipykernel_1599/1581105573.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  df_trade_lic['tradelicense_pure_w0'] = df_trade_lic['tradelicense_pure'].str.replace("\.0", "")


In [85]:
df_trade_lic

id  source_id         stable_id  \
0     70000001038141504          1 70000001038141504   
1     70000001038139640          1 70000001038139640   
2     70000001006487872          1 70000001006487872   
3     70000001031625136          1 70000001031625136   
4     70000001032892096          1 70000001032892096   
...                 ...        ...               ...   
69810 70000001039928304          1 70000001039928304   
69811 70000001034214128          1 70000001034214128   
69812 70000001028250992          1 70000001028250992   
69813 70000001032648656          1 70000001032648656   
69814 70000001006649704          1 70000001006649704   

                                                 name           firm_id  \
0                        Total Care Mobile Phones LLC 70000001038141504   
1                           Smart Tax Consultancy LLC 70000001038139640   
2                                      Vital Sign LLC 70000001006487872   
3      Al Shams Al Tahabiah Garments Ironing, laundry 70000001031625136   
4        Mohammed Kahteeri Gas District Establishment 70000001032892096   
...                                               ...               ...   
69810                         JF, restaurant and cafe 70000001039928304   
69811                         Layaly Adan, restaurant 70000001034214120   
69812        Gulfscape Technical Services Company LLC 70000001028250992   
69813                           Kanaan Decor, company 70000001032648648   
69814                           Selex Electricals LLC 70000001006649704   

                                            firm_name  branch_id tradelicense  \
0                        Total Care Mobile Phones LLC         99   CN-1795648   
1                           Smart Tax Consultancy LLC         99   CN-2433306   
2                                      Vital Sign LLC         99     650350.0   
3      Al Shams Al Tahabiah Garments Ironing, laundry         99     749204.0   
4        Mohammed Kahteeri Gas District Establishment         99   CN-1049336   
...                                               ...        ...          ...   
69810                         JF, restaurant and cafe         99   CN-2289775   
69811                         Layaly Adan, restaurant         99        93749   
69812        Gulfscape Technical Services Company LLC         99       746018   
69813                           Kanaan Decor, company         99   CN-1033065   
69814                           Selex Electricals LLC         99       554414   

          phone tradelicense_pure tradelicense_pure_w0  \
0     557130040           1795648              1795648   
1     507339118           2433306              2433306   
2       2383278            650350               650350   
3     502039685            749204               749204   
4           NaN           1049336              1049336   
...         ...               ...                  ...   
69810 523005997           2289775              2289775   
69811   2221227             93749                93749   
69812   2659835            746018               746018   
69813   5542867           1033065              1033065   
69814   2678714            554414               554414   

      tradelicense_pure_w0andCN  
0                       1795648  
1                       2433306  
2                        650350  
3                        749204  
4                       1049336  
...                         ...  
69810                   2289775  
69811                     93749  
69812                    746018  
69813                   1033065  
69814                    554414  

[69815 rows x 12 columns]

In [92]:
df_trade_lic_matched_master_trade_name = df_trade_lic.merge(df_lic_master.drop_duplicates(), left_on=['tradelicense_pure_w0andCN'], right_on=['trade_name_serial_number'], how='left', indicator='Ind1')

In [93]:
df_trade_lic_matched_master_license_number = df_trade_lic.merge(df_lic_master.drop_duplicates(), left_on=['tradelicense_pure_w0andCN'], right_on=['license_number'], how='left', indicator='Ind1')

In [ ]:
# matched

In [94]:
df_trade_lic_matched_master_license_number[df_trade_lic_matched_master_license_number['Ind1']=='both']

id  source_id         stable_id  \
2     70000001006487872          1 70000001006487872   
3     70000001031625136          1 70000001031625136   
11    70000001020593376          1 70000001020593376   
12    70000001042742552          1 70000001042742552   
14    70000001017285056          1 70000001017285056   
...                 ...        ...               ...   
69803 70000001032944128          1 70000001032944128   
69806 70000001040066176          1 70000001040066176   
69808 70000001038126552          1 70000001038126552   
69812 70000001028250992          1 70000001028250992   
69814 70000001006649704          1 70000001006649704   

                                                 name           firm_id  \
2                                      Vital Sign LLC 70000001006487872   
3      Al Shams Al Tahabiah Garments Ironing, laundry 70000001031625136   
11           Blue Force Pool Maintenance Services LLC 70000001020593376   
12                                    Abuagla, garage 70000001042742552   
14                                 Master Systems LLC 70000001017285048   
...                                               ...               ...   
69803         Beeta Petrolium Products & Supplies LLC 70000001032944128   
69806                    The Grill Street, restaurant 70000001040445680   
69808                        Bravo Awards & Gifts LLC 70000001032882816   
69812        Gulfscape Technical Services Company LLC 70000001028250992   
69814                           Selex Electricals LLC 70000001006649704   

                                            firm_name  branch_id tradelicense  \
2                                      Vital Sign LLC         99     650350.0   
3      Al Shams Al Tahabiah Garments Ironing, laundry         99     749204.0   
11           Blue Force Pool Maintenance Services LLC         99     628641.0   
12                                    Abuagla, garage         99     102906.0   
14                                 Master Systems LLC         99     683627.0   
...                                               ...        ...          ...   
69803         Beeta Petrolium Products & Supplies LLC         99   CN-1013734   
69806                    The Grill Street, restaurant         99       758530   
69808                        Bravo Awards & Gifts LLC         99   CN-1011315   
69812        Gulfscape Technical Services Company LLC         99       746018   
69814                           Selex Electricals LLC         99       554414   

          phone tradelicense_pure tradelicense_pure_w0  \
2       2383278            650350               650350   
3     502039685            749204               749204   
11      3368088            628641               628641   
12    507428986            102906               102906   
14    526930394            683627               683627   
...         ...               ...                  ...   
69803   6424013           1013734              1013734   
69806 569981444            758530               758530   
69808 529110909           1011315              1011315   
69812   2659835            746018               746018   
69814   2678714            554414               554414   

      tradelicense_pure_w0andCN license_number  issue_authority_code  \
2                        650350         650350                    83   
3                        749204         749204                    83   
11                       628641         628641                    83   
12                       102906         102906                    83   
14                       683627         683627                    88   
...                         ...            ...                   ...   
69803                   1013734        1013734                    83   
69806                    758530         758530                    83   
69808                   1011315        1011315                    83   
69812                    746018         746018           

In [95]:
df_trade_lic_matched_master_trade_name[df_trade_lic_matched_master_trade_name['Ind1']=='both']

id  source_id         stable_id  \
1     70000001038139640          1 70000001038139640   
4     70000001032892096          1 70000001032892096   
6     70000001038121424          1 70000001038121424   
7     70000001041164864          1 70000001041164864   
10    70000001046931776          1 70000001046931776   
...                 ...        ...               ...   
69810 70000001044135976          1 70000001044135976   
69815 70000001034512832          1 70000001034512832   
69821 70000001038121328          1 70000001038121328   
69825 70000001038126552          1 70000001038126552   
69830 70000001032648656          1 70000001032648656   

                                               name           firm_id  \
1                         Smart Tax Consultancy LLC 70000001038139640   
4      Mohammed Kahteeri Gas District Establishment 70000001032892096   
6                     Al Fares Taekwondo Center LLC 70000001038121416   
7                      Punjabi Dhaba Restaurant LLC 70000001041164864   
10            Couplers General Contracting, company 70000001046931776   
...                                             ...               ...   
69810               Ain Al Saqer Car Repair, garage 70000001044135976   
69815                         Ajman Cricket Council 70000001034512824   
69821            Al Dharis Recruitment Services EST 70000001038121320   
69825                      Bravo Awards & Gifts LLC 70000001032882816   
69830                         Kanaan Decor, company 70000001032648648   

                                          firm_name  branch_id tradelicense  \
1                         Smart Tax Consultancy LLC         99   CN-2433306   
4      Mohammed Kahteeri Gas District Establishment         99   CN-1049336   
6                     Al Fares Taekwondo Center LLC         99   CN-2164712   
7                      Punjabi Dhaba Restaurant LLC         99      42258.0   
10            Couplers General Contracting, company         99   CN-1781941   
...                                             ...        ...          ...   
69810               Ain Al Saqer Car Repair, garage         99   CN-1114784   
69815                         Ajman Cricket Council         99        14772   
69821            Al Dharis Recruitment Services EST         99   CN-1189122   
69825                      Bravo Awards & Gifts LLC         99   CN-1011315   
69830                         Kanaan Decor, company         99   CN-1033065   

          phone tradelicense_pure tradelicense_pure_w0  \
1     507339118           2433306              2433306   
4           NaN           1049336              1049336   
6       5544647           2164712              2164712   
7     558991486             42258                42258   
10    557223989           1781941              1781941   
...         ...               ...                  ...   
69810 507633302           1114784              1114784   
69815   7441450             14772                14772   
69821 506161235           1189122              1189122   
69825 529110909           1011315              1011315   
69830   5542867           1033065              1033065   

      tradelicense_pure_w0andCN license_number  issue_authority_code  \
1                       2433306         945182                    83   
4                       1049336         605320                    84   
6                       2164712         861414                    83   
7                         42258         209636                    83   
10                      1781941         770453                    83   
...                         ...            ...                   ...   
69810                   1114784         616296                    83   
69815                     14772         207165                    83   
69821                   1189122         562122                    83   
69825                   1011315         587742                    83   
69830                   1033065  

In [49]:
df_trade_lic_matched_master_trade_name[df_trade_lic_matched_master_trade_name['_merge']=='both'].groupby('firm_id').size().sort_values(ascending=False)

firm_id
7.000000e+16    17
7.000000e+16    14
7.000000e+16    12
7.000000e+16    12
7.000000e+16    11
                ..
7.000000e+16     1
7.000000e+16     1
7.000000e+16     1
7.000000e+16     1
7.000000e+16     1
Length: 19202, dtype: int64

In [96]:
# not_matched
df_trade_lic_merged = pd.concat([df_trade_lic_matched_master_license_number[df_trade_lic_matched_master_license_number['Ind1']=='both'], df_trade_lic_matched_master_trade_name[df_trade_lic_matched_master_trade_name['Ind1']=='both']])

In [97]:
df_trade_lic_merged

id  source_id         stable_id  \
2     70000001006487872          1 70000001006487872   
3     70000001031625136          1 70000001031625136   
11    70000001020593376          1 70000001020593376   
12    70000001042742552          1 70000001042742552   
14    70000001017285056          1 70000001017285056   
...                 ...        ...               ...   
69810 70000001044135976          1 70000001044135976   
69815 70000001034512832          1 70000001034512832   
69821 70000001038121328          1 70000001038121328   
69825 70000001038126552          1 70000001038126552   
69830 70000001032648656          1 70000001032648656   

                                                 name           firm_id  \
2                                      Vital Sign LLC 70000001006487872   
3      Al Shams Al Tahabiah Garments Ironing, laundry 70000001031625136   
11           Blue Force Pool Maintenance Services LLC 70000001020593376   
12                                    Abuagla, garage 70000001042742552   
14                                 Master Systems LLC 70000001017285048   
...                                               ...               ...   
69810                 Ain Al Saqer Car Repair, garage 70000001044135976   
69815                           Ajman Cricket Council 70000001034512824   
69821              Al Dharis Recruitment Services EST 70000001038121320   
69825                        Bravo Awards & Gifts LLC 70000001032882816   
69830                           Kanaan Decor, company 70000001032648648   

                                            firm_name  branch_id tradelicense  \
2                                      Vital Sign LLC         99     650350.0   
3      Al Shams Al Tahabiah Garments Ironing, laundry         99     749204.0   
11           Blue Force Pool Maintenance Services LLC         99     628641.0   
12                                    Abuagla, garage         99     102906.0   
14                                 Master Systems LLC         99     683627.0   
...                                               ...        ...          ...   
69810                 Ain Al Saqer Car Repair, garage         99   CN-1114784   
69815                           Ajman Cricket Council         99        14772   
69821              Al Dharis Recruitment Services EST         99   CN-1189122   
69825                        Bravo Awards & Gifts LLC         99   CN-1011315   
69830                           Kanaan Decor, company         99   CN-1033065   

          phone tradelicense_pure tradelicense_pure_w0  \
2       2383278            650350               650350   
3     502039685            749204               749204   
11      3368088            628641               628641   
12    507428986            102906               102906   
14    526930394            683627               683627   
...         ...               ...                  ...   
69810 507633302           1114784              1114784   
69815   7441450             14772                14772   
69821 506161235           1189122              1189122   
69825 529110909           1011315              1011315   
69830   5542867           1033065              1033065   

      tradelicense_pure_w0andCN license_number  issue_authority_code  \
2                        650350         650350                    83   
3                        749204         749204                    83   
11                       628641         628641                    83   
12                       102906         102906                    83   
14                       683627         683627                    88   
...                         ...            ...                   ...   
69810                   1114784         616296                    83   
69815                     14772         207165                    83   
69821                   1189122         562122                    83   
69825                   1011315         587742           

In [101]:
df_trade_lic_not_merged = df_trade_lic.merge(df_trade_lic_merged, on='firm_id', how='left', indicator='Ind')

In [104]:
df_trade_lic_not_merged[df_trade_lic_not_merged['Ind']== 'left_only']

id_x  source_id_x       stable_id_x  \
5      70000001042542336            1 70000001042542336   
8      70000001032080688            1 70000001032080688   
9      70000001032882688            1 70000001032882688   
30     70000001057812016            1 70000001057812016   
34     70000001006530624            1 70000001006530624   
...                  ...          ...               ...   
134378 70000001038136424            1 70000001038136424   
134380 70000001040476016            1 70000001040476016   
134383 70000001032882920            1 70000001032882920   
134384 70000001039928304            1 70000001039928304   
134385 70000001034214128            1 70000001034214128   

                                        name_x           firm_id  \
5                  Marina, cafe and restaurant 70000001042542336   
8                         Shafiq Interiors LLC 70000001032080688   
9            Long Way Fresh Meat Trading, shop 70000001032882688   
30           Capital Side Real Estate, company 70000001057812016   
34        EHRC Human Resources Consultancy LLC 70000001006530624   
...                                        ...               ...   
134378  Oriental Stone General Maintenance LLC 70000001038136424   
134380                      Soil Organic, shop 70000001040476016   
134383                   Golden Class, laundry 70000001032882920   
134384                 JF, restaurant and cafe 70000001039928304   
134385                 Layaly Adan, restaurant 70000001034214120   

                                   firm_name_x  branch_id_x tradelicense_x  \
5                  Marina, cafe and restaurant           99         5284.0   
8                         Shafiq Interiors LLC           99        69385.0   
9            Long Way Fresh Meat Trading, shop           99     CN-1185183   
30           Capital Side Real Estate, company           99     CN-3788819   
34        EHRC Human Resources Consultancy LLC           99      1700770.0   
...                                        ...          ...            ...   
134378  Oriental Stone General Maintenance LLC           99     CN-1170026   
134380                      Soil Organic, shop           99     CN-2698323   
134383                   Golden Class, laundry           99        1203323   
134384                 JF, restaurant and cafe           99     CN-2289775   
134385                 Layaly Adan, restaurant           99          93749   

         phone_x tradelicense_pure_x tradelicense_pure_w0_x  \
5        2441911                5284                   5284   
8      502121164               69385                  69385   
9      544652736             1185183                1185183   
30     504440493             3788819                3788819   
34     506074009             1700770                1700770   
...          ...                 ...                    ...   
134378   4446683             1170026                1170026   
134380 522995124             2698323                2698323   
134383 502806220             1203323                1203323   
134384 523005997             2289775                2289775   
134385   2221227               93749                  93749   

       tradelicense_pure_w0andCN_x  id_y  source_id_y  stable_id_y name_y  \
5                             5284   NaN          NaN          NaN    NaN   
8                            69385   NaN          NaN          NaN    NaN   
9                          1185183   NaN          NaN          NaN    NaN   
30                         3788819   NaN          NaN          NaN    NaN   
34                         1700770   NaN          NaN          NaN    NaN   
...                            ...   ...          ...          ...    ...   
134378                     1170026   NaN          NaN          NaN    NaN   
134380                     2698323   NaN          NaN          NaN    NaN   
134383                     1203323   NaN          NaN          NaN    NaN   
134384                     228

 #  Архив

In [ ]:
df_activities_master[df_activities_master['_merge'] != 'both']

In [78]:
df_trade_lic_CN = df_trade_lic[df_trade_lic['tradelicense'].str.contains('CN-')]

In [79]:
df_trade_lic_CN

id  source_id     stable_id  \
0      7.000000e+16          1  7.000000e+16   
1      7.000000e+16          1  7.000000e+16   
4      7.000000e+16          1  7.000000e+16   
6      7.000000e+16          1  7.000000e+16   
9      7.000000e+16          1  7.000000e+16   
...             ...        ...           ...   
69805  7.000000e+16          1  7.000000e+16   
69807  7.000000e+16          1  7.000000e+16   
69808  7.000000e+16          1  7.000000e+16   
69810  7.000000e+16          1  7.000000e+16   
69813  7.000000e+16          1  7.000000e+16   

                                               name       firm_id  \
0                      Total Care Mobile Phones LLC  7.000000e+16   
1                         Smart Tax Consultancy LLC  7.000000e+16   
4      Mohammed Kahteeri Gas District Establishment  7.000000e+16   
6                     Al Fares Taekwondo Center LLC  7.000000e+16   
9                 Long Way Fresh Meat Trading, shop  7.000000e+16   
...                                             ...           ...   
69805        Oriental Stone General Maintenance LLC  7.000000e+16   
69807                            Soil Organic, shop  7.000000e+16   
69808                      Bravo Awards & Gifts LLC  7.000000e+16   
69810                       JF, restaurant and cafe  7.000000e+16   
69813                         Kanaan Decor, company  7.000000e+16   

                                          firm_name  branch_id tradelicense  \
0                      Total Care Mobile Phones LLC         99   CN-1795648   
1                         Smart Tax Consultancy LLC         99   CN-2433306   
4      Mohammed Kahteeri Gas District Establishment         99   CN-1049336   
6                     Al Fares Taekwondo Center LLC         99   CN-2164712   
9                 Long Way Fresh Meat Trading, shop         99   CN-1185183   
...                                             ...        ...          ...   
69805        Oriental Stone General Maintenance LLC         99   CN-1170026   
69807                            Soil Organic, shop         99   CN-2698323   
69808                      Bravo Awards & Gifts LLC         99   CN-1011315   
69810                       JF, restaurant and cafe         99   CN-2289775   
69813                         Kanaan Decor, company         99   CN-1033065   

             phone  
0      557130040.0  
1      507339118.0  
4              NaN  
6        5544647.0  
9      544652736.0  
...            ...  
69805    4446683.0  
69807  522995124.0  
69808  529110909.0  
69810  523005997.0  
69813    5542867.0  

[13335 rows x 9 columns]

In [92]:
df_trade_lic_0 = df_trade_lic[df_trade_lic['tradelicense'].str.contains('\.0')]
df_trade_lic_0

Empty DataFrame
Columns: [id, source_id, stable_id, name, firm_id, firm_name, branch_id, tradelicense, phone]
Index: []

In [90]:
df_trade_lic['tradelicense'] = df_trade_lic['tradelicense'].str.replace("\.0", "")

/var/folders/5b/cfgbcxjj0n30b2ljslhwkz9mndjsxd/T/ipykernel_20358/135349007.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  df_trade_lic['tradelicense'] = df_trade_lic['tradelicense'].str.replace("\.0", "")


In [100]:
df_trade_lic.columns

Index(['id', 'source_id', 'stable_id', 'name', 'firm_id', 'firm_name',
       'branch_id', 'tradelicense', 'phone'],
      dtype='object')

In [104]:
df_trade_lic_CN['tradelicense_n'] = df_trade_lic_CN['tradelicense'].str.replace("CN-", "")

/var/folders/5b/cfgbcxjj0n30b2ljslhwkz9mndjsxd/T/ipykernel_20358/1438233175.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_trade_lic_CN['tradelicense_n'] = df_trade_lic_CN['tradelicense'].str.replace("CN-", "")


In [112]:
type(df_lic_master.trade_name_serial_number)

pandas.core.series.Series

In [120]:
df_trade_lic_CN['tradelicense_n'] = df_trade_lic_CN['tradelicense_n'].astype(str)

/var/folders/5b/cfgbcxjj0n30b2ljslhwkz9mndjsxd/T/ipykernel_20358/645165137.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_trade_lic_CN['tradelicense_n'] = df_trade_lic_CN['tradelicense_n'].astype(str)


In [136]:
df_trade_lic_CN

id  source_id     stable_id  \
0      7.000000e+16          1  7.000000e+16   
1      7.000000e+16          1  7.000000e+16   
4      7.000000e+16          1  7.000000e+16   
6      7.000000e+16          1  7.000000e+16   
9      7.000000e+16          1  7.000000e+16   
10     7.000000e+16          1  7.000000e+16   
18     7.000000e+16          1  7.000000e+16   
21     7.000000e+16          1  7.000000e+16   
26     7.000000e+16          1  7.000000e+16   
27     7.000000e+16          1  7.000000e+16   
40     7.000000e+16          1  7.000000e+16   
41     7.000000e+16          1  7.000000e+16   
48     7.000000e+16          1  7.000000e+16   
54     7.000000e+16          1  7.000000e+16   
65     7.000000e+16          1  7.000000e+16   
68     7.000000e+16          1  7.000000e+16   
69     7.000000e+16          1  7.000000e+16   
74     7.000000e+16          1  7.000000e+16   
76     7.000000e+16          1  7.000000e+16   
84     7.000000e+16          1  7.000000e+16   
89     7.000000e+16          1  7.000000e+16   
99     7.000000e+16          1  7.000000e+16   
102    7.000000e+16          1  7.000000e+16   
108    7.000000e+16          1  7.000000e+16   
111    7.000000e+16          1  7.000000e+16   
112    7.000000e+16          1  7.000000e+16   
127    7.000000e+16          1  7.000000e+16   
129    7.000000e+16          1  7.000000e+16   
136    7.000000e+16          1  7.000000e+16   
138    7.000000e+16          1  7.000000e+16   
146    7.000000e+16          1  7.000000e+16   
147    7.000000e+16          1  7.000000e+16   
148    7.000000e+16          1  7.000000e+16   
166    7.000000e+16          1  7.000000e+16   
167    7.000000e+16          1  7.000000e+16   
173    7.000000e+16          1  7.000000e+16   
174    7.000000e+16          1  7.000000e+16   
181    7.000000e+16          1  7.000000e+16   
190    7.000000e+16          1  7.000000e+16   
191    7.000000e+16          1  7.000000e+16   
197    7.000000e+16          1  7.000000e+16   
205    7.000000e+16          1  7.000000e+16   
206    7.000000e+16          1  7.000000e+16   
211    7.000000e+16          1  7.000000e+16   
212    7.000000e+16          1  7.000000e+16   
214    7.000000e+16          1  7.000000e+16   
220    7.000000e+16          1  7.000000e+16   
223    7.000000e+16          1  7.000000e+16   
226    7.000000e+16          1  7.000000e+16   
238    7.000000e+16          1  7.000000e+16   
239    7.000000e+16          1  7.000000e+16   
241    7.000000e+16          1  7.000000e+16   
253    7.000000e+16          1  7.000000e+16   
254    7.000000e+16          1  7.000000e+16   
259    7.000000e+16          1  7.000000e+16   
260    7.000000e+16          1  7.000000e+16   
263    7.000000e+16          1  7.000000e+16   
266    7.000000e+16          1  7.000000e+16   
267    7.000000e+16          1  7.000000e+16   
271    7.000000e+16          1  7.000000e+16   
272    7.000000e+16          1  7.000000e+16   
273    7.000000e+16          1  7.000000e+16   
277    7.000000e+16          1  7.000000e+16   
278    7.000000e+16          1  7.000000e+16   
279    7.000000e+16          1  7.000000e+16   
281    7.000000e+16          1  7.000000e+16   
283    7.000000e+16          1  7.000000e+16   
284    7.000000e+16          1  7.000000e+16   
292    7.000000e+16          1  7.000000e+16   
295    7.000000e+16          1  7.000000e+16   
296    7.000000e+16          1  7.000000e+16   
303    7.000000e+16          1  7.000000e+16   
307    7.000000e+16          1  7.000000e+16   
308    7.000000e+16          1  7.000000e+16   
309    7.000000e+16          1  7.000000e+16   
310    7.000000e+16          1  7.000000e+16   
312    7.000000e+16          1  7.000000e+16   
313    7.000000e+16          1  7.000000e+16   
314    7.000000e+16          1  7.000000e+16   
322    7.000000e+16          1  7.000000e+16   
325    7.000000e+16          1  7.000000e+16   
329    7.000000e+16          1  7.000000e+16   
336    7.000000e+16          1  7

In [155]:
df_lic_master['trade_name_serial_number'] = df_lic_master['trade_name_serial_number'].astype(str)
df_lic_master['license_number'] = df_lic_master['license_number'].astype(str)

In [142]:
len(df_lic_master)

538471

In [148]:
df_merge_lic_master_trade_lic = df_trade_lic_CN.merge(df_lic_master, left_on='tradelicense_n', right_on='trade_name_serial_number', how='outer', indicator=True)

In [152]:
df_merge_lic_master_trade_lic[df_merge_lic_master_trade_lic['_merge']=='left_only']

id  source_id     stable_id  \
0      7.000000e+16        1.0  7.000000e+16   
5      7.000000e+16        1.0  7.000000e+16   
6      7.000000e+16        1.0  7.000000e+16   
8      7.000000e+16        1.0  7.000000e+16   
9      7.000000e+16        1.0  7.000000e+16   
...             ...        ...           ...   
13327  7.000000e+16        1.0  7.000000e+16   
13328  7.000000e+16        1.0  7.000000e+16   
13330  7.000000e+16        1.0  7.000000e+16   
13331  7.000000e+16        1.0  7.000000e+16   
13333  7.000000e+16        1.0  7.000000e+16   

                                          name       firm_id  \
0                 Total Care Mobile Phones LLC  7.000000e+16   
5            Long Way Fresh Meat Trading, shop  7.000000e+16   
6                    Long Way Fresh, meat shop  7.000000e+16   
8                     Caltrols Middle East LLC  7.000000e+16   
9            Capital Side Real Estate, company  7.000000e+16   
...                                        ...           ...   
13327           Al Shameel Health Care, centre  7.000000e+16   
13328  Beeta Petrolium Products & Supplies LLC  7.000000e+16   
13330   Oriental Stone General Maintenance LLC  7.000000e+16   
13331                       Soil Organic, shop  7.000000e+16   
13333                  JF, restaurant and cafe  7.000000e+16   

                                     firm_name  branch_id tradelicense  \
0                 Total Care Mobile Phones LLC       99.0   CN-1795648   
5            Long Way Fresh Meat Trading, shop       99.0   CN-1185183   
6                    Long Way Fresh, meat shop       99.0   CN-1185183   
8                     Caltrols Middle East LLC       99.0   CN-1186426   
9            Capital Side Real Estate, company       99.0   CN-3788819   
...                                        ...        ...          ...   
13327           Al Shameel Health Care, centre       99.0   CN-2008643   
13328  Beeta Petrolium Products & Supplies LLC       99.0   CN-1013734   
13330   Oriental Stone General Maintenance LLC       99.0   CN-1170026   
13331                       Soil Organic, shop       99.0   CN-2698323   
13333                  JF, restaurant and cafe       99.0   CN-2289775   

             phone tradelicense_n  license_number  issue_authority_code  \
0      557130040.0        1795648             NaN                   NaN   
5      544652736.0        1185183             NaN                   NaN   
6      505963942.0        1185183             NaN                   NaN   
8        5509901.0        1186426             NaN                   NaN   
9      504440493.0        3788819             NaN                   NaN   
...            ...            ...             ...                   ...   
13327  561509051.0        2008643             NaN                   NaN   
13328    6424013.0        1013734             NaN                   NaN   
13330    4446683.0        1170026             NaN                   NaN   
13331  522995124.0        2698323             NaN                   NaN   
13333  523005997.0        2289775             NaN                   NaN   

      issue_authority_desc_ar issue_authority_desc_en  \
0                         NaN                     NaN   
5                         NaN                     NaN   
6                         NaN                     NaN   
8                         NaN                     NaN   
9                         NaN                     NaN   
...                       ...                     ...   
13327                     NaN                     NaN   
13328                     NaN                     NaN   
13330                     NaN                     NaN   
13331                     NaN                     NaN   
13333                     NaN                     NaN   

       issue_authority_license_number  initial_approval_number  \
0                                 NaN                      NaN   
5                                 NaN                      NaN  

In [156]:
df_trade_lic_CN.merge(df_lic_master, left_on='tradelicense_n', right_on='license_number', how='inner')

id  source_id     stable_id  \
0     7.000000e+16          1  7.000000e+16   
1     7.000000e+16          1  7.000000e+16   
2     7.000000e+16          1  7.000000e+16   
3     7.000000e+16          1  7.000000e+16   
4     7.000000e+16          1  7.000000e+16   
...            ...        ...           ...   
1169  7.000000e+16          1  7.000000e+16   
1170  7.000000e+16          1  7.000000e+16   
1171  7.000000e+16          1  7.000000e+16   
1172  7.000000e+16          1  7.000000e+16   
1173  7.000000e+16          1  7.000000e+16   

                                                name       firm_id  \
0                          Beauty Touch Ladies Salon  7.000000e+16   
1            Clouds Ray General Maintenance, company  7.000000e+16   
2           Al Thaniyya Cattle & Sheep Trading, shop  7.000000e+16   
3           Al Shagga & Brothers Trading Company LLC  7.000000e+16   
4                             Al Sada Cargo, company  7.000000e+16   
...                                              ...           ...   
1169                              Arab Beverages LLC  7.000000e+16   
1170  Currie & Brown, management consultancy company  7.000000e+16   
1171                       Abu Dhabi Marketing Group  7.000000e+16   
1172         Beeta Petrolium Products & Supplies LLC  7.000000e+16   
1173                        Bravo Awards & Gifts LLC  7.000000e+16   

                                           firm_name  branch_id tradelicense  \
0                          Beauty Touch Ladies Salon         99   CN-1019441   
1            Clouds Ray General Maintenance, company         99   CN-1012328   
2           Al Thaniyya Cattle & Sheep Trading, shop         99   CN-1009235   
3           Al Shagga & Brothers Trading Company LLC         99   CN-1016202   
4                             Al Sada Cargo, company         99   CN-1002689   
...                                              ...        ...          ...   
1169                              Arab Beverages LLC         99   CN-1018830   
1170  Currie & Brown, management consultancy company         99   CN-1001351   
1171                       Abu Dhabi Marketing Group         99   CN-1018072   
1172         Beeta Petrolium Products & Supplies LLC         99   CN-1013734   
1173                        Bravo Awards & Gifts LLC         99   CN-1011315   

            phone tradelicense_n license_number  issue_authority_code  \
0       4455039.0        1019441        1019441                    83   
1     507821636.0        1012328        1012328                    83   
2     505665003.0        1009235        1009235                    83   
3       6335088.0        1016202        1016202                    83   
4       6716966.0        1002689        1002689                    91   
...           ...            ...            ...                   ...   
1169    8867288.0        1018830        1018830                    83   
1170    6716265.0        1001351        1001351                    83   
1171  506162122.0        1018072        1018072                    83   
1172    6424013.0        1013734        1013734                    83   
1173  529110909.0        1011315        1011315                    83   

       issue_authority_desc_ar       issue_authority_desc_en  \
0     دائرة التنمية الاقتصادية  Dep. of Economic Development   
1     دائرة التنمية الاقتصادية  Dep. of Economic Development   
2     دائرة التنمية الاقتصادية  Dep. of Economic Development   
3     دائرة التنمية الاقتصادية  Dep. of Economic Development   
4       رخصة التاجر الإلكتروني             e-Traders License   
...                        ...                           ...   
1169  دائرة التنمية الاقتصادية  Dep. of Economic Development   
1170  دائرة التنمية الاقتصادية  Dep. of Economic Development   
1171  دائرة التنمية الاقتصادية  Dep. of Economic Development   
1172  دائرة التنمية الاقتصادية  Dep. of Economic Development   
1173  دائرة التنمية الاقتصادية  Dep. of Economic Development   

   

In [158]:
df_lic_activities['license_number']  = df_lic_activities['license_number'].astype(str)

In [159]:
df_trade_lic_CN.merge(df_lic_activities, left_on='tradelicense_n', right_on='license_number', how='inner')

id  source_id     stable_id  \
0     7.000000e+16          1  7.000000e+16   
1     7.000000e+16          1  7.000000e+16   
2     7.000000e+16          1  7.000000e+16   
3     7.000000e+16          1  7.000000e+16   
4     7.000000e+16          1  7.000000e+16   
...            ...        ...           ...   
3791  7.000000e+16          1  7.000000e+16   
3792  7.000000e+16          1  7.000000e+16   
3793  7.000000e+16          1  7.000000e+16   
3794  7.000000e+16          1  7.000000e+16   
3795  7.000000e+16          1  7.000000e+16   

                                         name       firm_id  \
0                   Beauty Touch Ladies Salon  7.000000e+16   
1     Clouds Ray General Maintenance, company  7.000000e+16   
2     Clouds Ray General Maintenance, company  7.000000e+16   
3     Clouds Ray General Maintenance, company  7.000000e+16   
4     Clouds Ray General Maintenance, company  7.000000e+16   
...                                       ...           ...   
3791                 Bravo Awards & Gifts LLC  7.000000e+16   
3792                 Bravo Awards & Gifts LLC  7.000000e+16   
3793                 Bravo Awards & Gifts LLC  7.000000e+16   
3794                 Bravo Awards & Gifts LLC  7.000000e+16   
3795                 Bravo Awards & Gifts LLC  7.000000e+16   

                                    firm_name  branch_id tradelicense  \
0                   Beauty Touch Ladies Salon         99   CN-1019441   
1     Clouds Ray General Maintenance, company         99   CN-1012328   
2     Clouds Ray General Maintenance, company         99   CN-1012328   
3     Clouds Ray General Maintenance, company         99   CN-1012328   
4     Clouds Ray General Maintenance, company         99   CN-1012328   
...                                       ...        ...          ...   
3791                 Bravo Awards & Gifts LLC         99   CN-1011315   
3792                 Bravo Awards & Gifts LLC         99   CN-1011315   
3793                 Bravo Awards & Gifts LLC         99   CN-1011315   
3794                 Bravo Awards & Gifts LLC         99   CN-1011315   
3795                 Bravo Awards & Gifts LLC         99   CN-1011315   

            phone tradelicense_n  activity_code  \
0       4455039.0        1019441         741415   
1     507821636.0        1012328         513113   
2     507821636.0        1012328         513941   
3     507821636.0        1012328         513942   
4     507821636.0        1012328         513944   
...           ...            ...            ...   
3791  529110909.0        1011315         515102   
3792  529110909.0        1011315         515103   
3793  529110909.0        1011315         515104   
3794  529110909.0        1011315         515205   
3795  529110909.0        1011315         515207   

                                    activity_desc_ar  \
0                              إدارة العلاقات العامة   
1                            تجارة الملابس  الرياضية   
2                    تجارة المعدات والادوات الرياضية   
3          تجارة عتاد الخيل وادوات الفروسية ولوازمها   
4                         تجارة لوازم وادوات الرحلات   
...                                              ...   
3791    تجارة نظم وبرامج الحاسب الآلي وأجهزة الإتصال   
3792    تجارة مستلزمات الحاسب الآلي ومعالجة البيانات   
3793                تجارة اجهزة الحاسب الآلي ولوازمه   
3794  تجارة قطع غيار الاجهزة الكهربائية والالكترونية   
3795                 تجارة الهواتف المتحركة ولوازمها   

                                       activity_desc_en  activity_status_code  \
0                           Public relations Management                     0   
1                                   Sports Wear Trading                     0   
2                               Sport Equipment Trading                     0   
3       Horse Equestrian Equipment & Requisites Trading                     0   
4                            Camping Requisites Trading                     0   
...                                          